# Training a Linear Regression Model to Predict GPU Performance 

Welcome to our programming project! This is where you'll get to apply the knowledge you obtained in class on a real world project. While the demos are done using SKLearn for simplicity, these programming projects aim to expose you to PyTorch, an industrial library for Machine Learning.


## Introduction

The GPU is a piece of computing hardware first developed in the early 1990s for accelerating graphical applications. Due to its highly parallel nature, people eventually found great uses of GPUs in areas other than gaming. Today, the GPU market is a 20 billion dollar market that serves the fields of video games, AI, crypto, scientific computing and engineering sectors.

In this project, we will train a linear regression model on a GPU dataset -- our goal is to build a web application that takes in the **process node, die area, memory size,** and the number of **millions of transistors** to predict the **compute performance** of that GPU.

## Importing the Necessary Libraries

This project aims to train a linear regression model on the **AMD Radeon and Nvidia GPU Specifications** dataset by  JetBrains Datalore. Here are a list of libraries used in this project:

- **PyTorch**: A powerful machine learning Library
- **PyTorch Lightning**: We only use it for its R2score function
- **Pandas** and **Numpy**: Used for easy data storage and linear algebra
- **SKLearn**: Train test split 
- **Matplotlib** and **Bokeh**: For creating static and dynamic visualizations

In [1]:
import torch
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from bokeh.plotting import show, figure, output_notebook


pd.set_option('display.max_colwidth', None)

## Loading the Dataset

The first step is to load and visualize the  dataset. This is crucial in any machine learning development process, as this can give you an idea of what features to include or exclude.

In [2]:
gpu_dataset = pd.read_csv("datasets/gpus_v2.csv")
gpu_dataset = gpu_dataset.sample(frac=1).reset_index(drop=True)
gpu_dataset.head(30)

Manufacturer        Class                    Name  Year  Fab  \
0        Nvidia  Workstation               RTX A6000  2020    8   
1    AMD Radeon      Desktop          Radeon HD 8760  2013   28   
2    AMD Radeon  Workstation      Radeon Pro WX 7100  2016   14   
3        Nvidia  Workstation           Quadro FX 380  2009   65   
4        Nvidia      Desktop        GeForce 8600 GTS  2007   80   
5    AMD Radeon  Workstation      Radeon Pro WX 5100  2016   14   
6    AMD Radeon  Workstation          FirePro V7800P  2011   40   
7        Nvidia  Workstation            Quadro P4000  2017   16   
8        Nvidia  Workstation            Quadro GV100  2018   12   
9        Nvidia   Datacenter               Tesla M40  2015   28   
10   AMD Radeon      Desktop          Radeon HD 4850  2008   55   
11   AMD Radeon   Datacenter          FirePro S10000  2012   28   
12       Nvidia   Datacenter  NVIDIA Tesla V100 FHHL  2018   12   
13       Nvidia   Datacenter               Tesla M10  2016   28   
14   AMD Radeon      Desktop           Radeon RX 550  2017   14   
15       Nvidia      Desktop        GeForce GTX 1060  2018   16   
16       Nvidia      Desktop        GeForce GTX 1050  2018   14   
17   AMD Radeon      Desktop          Radeon HD 3470  2008   55   
18       Nvidia  Workstation            Quadro P2000  2017   16   
19       Nvidia  Workstation            Quadro K2200  2014   28   
20   AMD Radeon  Workstation           FirePro V4900  2011   40   
21       Nvidia      Desktop        GeForce GTX 1080  2017   16   
22       Nvidia   Datacenter               Tesla K80  2014   28   
23   AMD Radeon  Workstation      Radeon Pro WX 3200  2019   14   
24       Nvidia      Desktop         GeForce GTS 280  2008   65   
25       Nvidia      Desktop         GeForce 9500 GT  2008   65   
26       Nvidia   Datacenter             Tesla C2050  2011   40   
27   AMD Radeon  Workstation           FirePro W7000  2012   28   
28   AMD Radeon   Datacenter   Radeon Instinct MI100  2020    7   
29   AMD Radeon      Desktop          Radeon HD 4870  2008   55   

    Transistors (mln)  Die size  Memory size  Memory speed   GFLOPS    TDP  
0               28300       628        49152        768.00  40000.0  300.0  
1                1500       123         2048         72.00   1280.0   80.0  
2                5700       232         8192        256.00   5710.0  130.0  
3                 314       144          256         22.40     35.2   34.0  
4                 289       169          512         32.00     92.8   71.0  
5                5700       232         8192        211.20   3910.0   75.0  
6                2154       334         2048        128.00   2016.0  138.0  
7                7200       314         8192        243.30   5304.0  105.0  
8               21100       815        32768        868.40  16660.0  250.0  
9                8000       601        12288        288.40   6844.0  250.0  
10                956       256         2048         63.55   1000.0  110.0  
11               4313       352         6144        480.00   6810.0  375.0  
12              21100       815        16384        829.40  13210.0  250.0  
13               7480       592        32768        332.80   6688.0  225.0  
14               2200       101         4096        112.00   1211.0   50.0  
15               7200       314         6144        192.00   4375.0  200.0  
16               3300       132         3072         84.00   2331.6  120.0  
17                181        67          512         15.20     64.0   30.0  
18               4400       200         5120        140.20   3031.0   75.0  
19               1870       148         4096         80.19   1439.0   68.0  
20                716       118         1024         64.00    768.0   75.0  
21               7200       314         8192        352.00   8872.9  300.0  
22               7100       561        24576        481.20   8226.0  300.0  
23               2200       103         4096         96.00   1658.0   65.0  


Here, we are going to choose the columns `Transistors (mln)`, `Die size`, `Memory size` and `Fab` to be our **training features** and `GFLOPS` to be our **labels**.

In [3]:
# Creating np.arrays containing our training features and labels
features = gpu_dataset[["Transistors (mln)", "Die size", "Memory size", "Fab"]].to_numpy()
labels = gpu_dataset[['GFLOPS']].to_numpy()

print(f"features shape: {features.shape}")
print(f"labels shape: {labels.shape}\n")

# Train test split
X_train, X_test, Y_train, Y_test = train_test_split(features, labels, test_size=0.1)


print(f"X_train shape: {X_train.shape}")
print(f"Y_train shape: {Y_train.shape}")
print(f"X_test shape: {X_test.shape}")
print(f"Y_test shape: {Y_test.shape}")


features shape: (497, 4)
labels shape: (497, 1)

X_train shape: (447, 4)
Y_train shape: (447, 1)
X_test shape: (50, 4)
Y_test shape: (50, 1)


## Prototyping Our First Model (Multi-variate Linear Regression)

Our first model is going to perform Multi-variate linear regression on the data. In PyTorch, we actually have to define our own class (which is a subclass of torch.nn.Module) as well as its `forward()` function.

In [4]:
from torch.nn import Module, MSELoss, Linear
from torch.optim import SGD

class Linreg(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        """
        Args:
            inputs (int): the input dimensions
            outputs (int): the output dimensions
        """
        
        self.linear = Linear(inputs, outputs)      
        
    def forward(self, x):
        """
        The forward propagation method. This method is used
        by the torch.nn.Module subclass when training or evaluating
        """
        y_pred = self.linear(x)
        return y_pred
    

In [5]:
input_dims, output_dims = (X_train.shape[1], Y_train.shape[1])

# Epochs is the number of passes over our training set
learning_rate = 0.000000005
epochs = 50000

In [6]:
model = Linreg(input_dims, output_dims)

# Optimizing algorithm and loss (optimizing criterion)
optimizer = SGD(model.parameters(), lr=learning_rate)
loss = MSELoss()

In [7]:
# Must convert np.array to torch.tensor
inputs = torch.from_numpy(X_train).float()
labels = torch.from_numpy(Y_train).float()

# We need to import certain elements of this notebook 
# into a python file. if __name__ == "__main__" prevents these
# sections from running when importing, as it is computationally
# expensive
if __name__ == "__main__":
    for i in range(epochs):
        
        # clears gradient buffer from previous iteration
        model.zero_grad()
        # Feed forward
        pred = model(inputs)
        # Calcluate errors
        errors = loss(pred, labels)
        print(f"loss of iteration {i+1}: {errors}")
        # Backpropagation
        errors.backward()
        # update parameters
        optimizer.step()
    
    

loss of iteration 1: 37288340.0
loss of iteration 2: 30091532.0
loss of iteration 3: 24595462.0
loss of iteration 4: 20398074.0
loss of iteration 5: 17192458.0
loss of iteration 6: 14744157.0
loss of iteration 7: 12874222.0
loss of iteration 8: 11445954.0
loss of iteration 9: 10354987.0
loss of iteration 10: 9521625.0
loss of iteration 11: 8885002.0
loss of iteration 12: 8398646.0
loss of iteration 13: 8027059.5
loss of iteration 14: 7743136.0
loss of iteration 15: 7526167.5
loss of iteration 16: 7360346.0
loss of iteration 17: 7233595.5
loss of iteration 18: 7136690.5
loss of iteration 19: 7062583.0
loss of iteration 20: 7005897.0
loss of iteration 21: 6962518.0
loss of iteration 22: 6929305.0
loss of iteration 23: 6903863.0
loss of iteration 24: 6884355.0
loss of iteration 25: 6869382.5
loss of iteration 26: 6857877.5
loss of iteration 27: 6849021.0
loss of iteration 28: 6842190.5
loss of iteration 29: 6836905.5
loss of iteration 30: 6832805.0
loss of iteration 31: 6829607.0
loss of 

loss of iteration 603: 6710435.0
loss of iteration 604: 6710299.0
loss of iteration 605: 6710162.5
loss of iteration 606: 6710027.5
loss of iteration 607: 6709893.0
loss of iteration 608: 6709756.5
loss of iteration 609: 6709620.5
loss of iteration 610: 6709486.0
loss of iteration 611: 6709351.0
loss of iteration 612: 6709215.5
loss of iteration 613: 6709081.5
loss of iteration 614: 6708948.0
loss of iteration 615: 6708812.0
loss of iteration 616: 6708678.5
loss of iteration 617: 6708545.5
loss of iteration 618: 6708410.5
loss of iteration 619: 6708276.5
loss of iteration 620: 6708144.0
loss of iteration 621: 6708010.0
loss of iteration 622: 6707877.0
loss of iteration 623: 6707743.0
loss of iteration 624: 6707609.0
loss of iteration 625: 6707478.0
loss of iteration 626: 6707345.0
loss of iteration 627: 6707213.0
loss of iteration 628: 6707079.5
loss of iteration 629: 6706947.5
loss of iteration 630: 6706815.0
loss of iteration 631: 6706683.5
loss of iteration 632: 6706551.5
loss of it

loss of iteration 1221: 6649790.0
loss of iteration 1222: 6649722.5
loss of iteration 1223: 6649654.5
loss of iteration 1224: 6649585.5
loss of iteration 1225: 6649518.5
loss of iteration 1226: 6649451.0
loss of iteration 1227: 6649382.0
loss of iteration 1228: 6649315.0
loss of iteration 1229: 6649246.0
loss of iteration 1230: 6649181.0
loss of iteration 1231: 6649112.5
loss of iteration 1232: 6649044.5
loss of iteration 1233: 6648978.0
loss of iteration 1234: 6648911.0
loss of iteration 1235: 6648843.0
loss of iteration 1236: 6648776.5
loss of iteration 1237: 6648709.5
loss of iteration 1238: 6648643.0
loss of iteration 1239: 6648576.5
loss of iteration 1240: 6648508.5
loss of iteration 1241: 6648442.5
loss of iteration 1242: 6648376.0
loss of iteration 1243: 6648309.0
loss of iteration 1244: 6648242.5
loss of iteration 1245: 6648177.0
loss of iteration 1246: 6648109.0
loss of iteration 1247: 6648044.0
loss of iteration 1248: 6647977.5
loss of iteration 1249: 6647912.0
loss of iterat

loss of iteration 1856: 6618592.5
loss of iteration 1857: 6618557.5
loss of iteration 1858: 6618525.0
loss of iteration 1859: 6618490.0
loss of iteration 1860: 6618457.0
loss of iteration 1861: 6618422.0
loss of iteration 1862: 6618387.5
loss of iteration 1863: 6618353.5
loss of iteration 1864: 6618320.5
loss of iteration 1865: 6618286.0
loss of iteration 1866: 6618252.5
loss of iteration 1867: 6618218.5
loss of iteration 1868: 6618184.5
loss of iteration 1869: 6618151.5
loss of iteration 1870: 6618117.0
loss of iteration 1871: 6618084.0
loss of iteration 1872: 6618050.0
loss of iteration 1873: 6618016.0
loss of iteration 1874: 6617982.5
loss of iteration 1875: 6617950.0
loss of iteration 1876: 6617916.0
loss of iteration 1877: 6617883.0
loss of iteration 1878: 6617849.0
loss of iteration 1879: 6617815.0
loss of iteration 1880: 6617782.0
loss of iteration 1881: 6617749.0
loss of iteration 1882: 6617714.5
loss of iteration 1883: 6617681.5
loss of iteration 1884: 6617649.5
loss of iterat

loss of iteration 2540: 6601814.0
loss of iteration 2541: 6601798.0
loss of iteration 2542: 6601780.5
loss of iteration 2543: 6601764.0
loss of iteration 2544: 6601747.0
loss of iteration 2545: 6601728.5
loss of iteration 2546: 6601712.5
loss of iteration 2547: 6601695.0
loss of iteration 2548: 6601678.0
loss of iteration 2549: 6601661.5
loss of iteration 2550: 6601644.5
loss of iteration 2551: 6601628.0
loss of iteration 2552: 6601610.0
loss of iteration 2553: 6601594.0
loss of iteration 2554: 6601577.0
loss of iteration 2555: 6601560.0
loss of iteration 2556: 6601543.0
loss of iteration 2557: 6601526.5
loss of iteration 2558: 6601510.0
loss of iteration 2559: 6601494.0
loss of iteration 2560: 6601476.0
loss of iteration 2561: 6601459.0
loss of iteration 2562: 6601441.5
loss of iteration 2563: 6601425.5
loss of iteration 2564: 6601409.5
loss of iteration 2565: 6601393.0
loss of iteration 2566: 6601376.0
loss of iteration 2567: 6601358.5
loss of iteration 2568: 6601342.5
loss of iterat

...

loss of iteration 46415: 6492686.5
loss of iteration 46416: 6492685.5
loss of iteration 46417: 6492683.5
loss of iteration 46418: 6492681.0
loss of iteration 46419: 6492680.0
loss of iteration 46420: 6492678.5
loss of iteration 46421: 6492677.0
loss of iteration 46422: 6492674.5
loss of iteration 46423: 6492673.5
loss of iteration 46424: 6492672.0
loss of iteration 46425: 6492670.5
loss of iteration 46426: 6492669.0
loss of iteration 46427: 6492666.5
loss of iteration 46428: 6492664.5
loss of iteration 46429: 6492663.0
loss of iteration 46430: 6492662.5
loss of iteration 46431: 6492659.5
loss of iteration 46432: 6492657.5
loss of iteration 46433: 6492657.0
loss of iteration 46434: 6492655.0
loss of iteration 46435: 6492653.5
loss of iteration 46436: 6492651.5
loss of iteration 46437: 6492649.0
loss of iteration 46438: 6492648.0
loss of iteration 46439: 6492646.0
loss of iteration 46440: 6492644.5
loss of iteration 46441: 6492644.0
loss of iteration 46442: 6492642.0
loss of iteration 46

loss of iteration 47174: 6491419.5
loss of iteration 47175: 6491419.0
loss of iteration 47176: 6491417.0
loss of iteration 47177: 6491415.5
loss of iteration 47178: 6491414.0
loss of iteration 47179: 6491412.0
loss of iteration 47180: 6491411.0
loss of iteration 47181: 6491410.0
loss of iteration 47182: 6491406.5
loss of iteration 47183: 6491405.0
loss of iteration 47184: 6491404.0
loss of iteration 47185: 6491401.0
loss of iteration 47186: 6491400.5
loss of iteration 47187: 6491398.5
loss of iteration 47188: 6491397.0
loss of iteration 47189: 6491395.5
loss of iteration 47190: 6491395.0
loss of iteration 47191: 6491392.0
loss of iteration 47192: 6491391.5
loss of iteration 47193: 6491388.5
loss of iteration 47194: 6491387.5
loss of iteration 47195: 6491385.0
loss of iteration 47196: 6491383.5
loss of iteration 47197: 6491382.5
loss of iteration 47198: 6491380.5
loss of iteration 47199: 6491379.5
loss of iteration 47200: 6491377.0
loss of iteration 47201: 6491375.0
loss of iteration 47

loss of iteration 47937: 6490158.5
loss of iteration 47938: 6490156.5
loss of iteration 47939: 6490155.0
loss of iteration 47940: 6490154.5
loss of iteration 47941: 6490152.0
loss of iteration 47942: 6490150.5
loss of iteration 47943: 6490150.0
loss of iteration 47944: 6490147.5
loss of iteration 47945: 6490144.5
loss of iteration 47946: 6490143.5
loss of iteration 47947: 6490143.0
loss of iteration 47948: 6490140.5
loss of iteration 47949: 6490139.5
loss of iteration 47950: 6490137.0
loss of iteration 47951: 6490135.5
loss of iteration 47952: 6490134.5
loss of iteration 47953: 6490132.0
loss of iteration 47954: 6490130.0
loss of iteration 47955: 6490129.0
loss of iteration 47956: 6490127.0
loss of iteration 47957: 6490125.5
loss of iteration 47958: 6490123.0
loss of iteration 47959: 6490123.0
loss of iteration 47960: 6490120.5
loss of iteration 47961: 6490119.5
loss of iteration 47962: 6490118.5
loss of iteration 47963: 6490115.5
loss of iteration 47964: 6490114.5
loss of iteration 47

loss of iteration 48671: 6488955.5
loss of iteration 48672: 6488953.5
loss of iteration 48673: 6488952.5
loss of iteration 48674: 6488949.5
loss of iteration 48675: 6488947.5
loss of iteration 48676: 6488947.0
loss of iteration 48677: 6488946.0
loss of iteration 48678: 6488943.0
loss of iteration 48679: 6488943.0
loss of iteration 48680: 6488940.0
loss of iteration 48681: 6488938.5
loss of iteration 48682: 6488937.5
loss of iteration 48683: 6488935.5
loss of iteration 48684: 6488933.5
loss of iteration 48685: 6488932.0
loss of iteration 48686: 6488930.5
loss of iteration 48687: 6488929.0
loss of iteration 48688: 6488926.5
loss of iteration 48689: 6488925.5
loss of iteration 48690: 6488923.5
loss of iteration 48691: 6488922.5
loss of iteration 48692: 6488920.0
loss of iteration 48693: 6488918.5
loss of iteration 48694: 6488918.0
loss of iteration 48695: 6488916.0
loss of iteration 48696: 6488914.5
loss of iteration 48697: 6488913.5
loss of iteration 48698: 6488911.0
loss of iteration 48

loss of iteration 49471: 6487655.5
loss of iteration 49472: 6487654.5
loss of iteration 49473: 6487652.0
loss of iteration 49474: 6487651.5
loss of iteration 49475: 6487649.0
loss of iteration 49476: 6487647.5
loss of iteration 49477: 6487646.0
loss of iteration 49478: 6487645.0
loss of iteration 49479: 6487643.5
loss of iteration 49480: 6487641.5
loss of iteration 49481: 6487640.0
loss of iteration 49482: 6487639.0
loss of iteration 49483: 6487636.0
loss of iteration 49484: 6487635.0
loss of iteration 49485: 6487633.0
loss of iteration 49486: 6487632.0
loss of iteration 49487: 6487631.0
loss of iteration 49488: 6487627.5
loss of iteration 49489: 6487626.5
loss of iteration 49490: 6487624.5
loss of iteration 49491: 6487623.5
loss of iteration 49492: 6487621.5
loss of iteration 49493: 6487620.0
loss of iteration 49494: 6487619.0
loss of iteration 49495: 6487617.5
loss of iteration 49496: 6487615.5
loss of iteration 49497: 6487613.5
loss of iteration 49498: 6487611.5
loss of iteration 49

In [8]:
from pytorch_lightning.metrics.functional import r2score

# Must convert from np.array to torch.tensor 
test_inputs = torch.from_numpy(X_test).float()
test_labels = torch.from_numpy(Y_test).float()

# Sets model to evaluation mode. Evaluation mode turns off
# certain layers such as dropout or batch-norm, as these
# behave differently while training.
model.eval()

# predict and print r2 score
with torch.no_grad():
    test_pred = model(test_inputs)
    r2 = r2score(test_pred, test_labels)
    print(r2.item())

0.8537035584449768


### Observations

Our first attempt at training a linear regression model provided us with a few observations to note. First is that the loss is huge, even after gradient descent. This is because we are working with huge labels and our output space is very large, so do not be alarmed by the loss. It is better to note the R2 score, which our first model achieved 74%, which is fairly good. Lets fill in the observation table:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |


## Prototyping Our Second Model (Polynomial Regression)

We are going to train a second model, this time using polynomial regression with cubic features. This in theory should be able to fit a more complicated function to the data.

In [9]:
poly = PolynomialFeatures(degree=3)

# convert to polynomial features
X_train_p = poly.fit_transform(X_train)
X_test_p = poly.fit_transform(X_test)
Y_train_p = Y_train
Y_test_p = Y_test

print(f"X_train_p shape: {X_train_p.shape}")
print(f"Y_train_p shape: {Y_train_p.shape}")
print(f"X_test_p shape: {X_test_p.shape}")
print(f"Y_test_p shape: {Y_test_p.shape}")

X_train_p shape: (447, 35)
Y_train_p shape: (447, 1)
X_test_p shape: (50, 35)
Y_test_p shape: (50, 1)


In [10]:
# batch norm is used to normalize the inputs. Don't worry about 
# Explaining this to students, as it will be covered in a later topic
from torch.nn import BatchNorm1d

class Linreg_p(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        self.linear = Linear(inputs, outputs) 
        self.bn = BatchNorm1d(inputs)
        
    def forward(self, x):
        x = self.bn(x)
        y_pred = self.linear(x)
        return y_pred

In [11]:
input_dims_p, output_dims_p = (X_train_p.shape[1], Y_train_p.shape[1])
learning_rate_p = 0.000001
epochs_p = 50000

In [12]:
model_p = Linreg_p(input_dims_p, output_dims_p)

# Optimizer and loss
optimizer_p = SGD(model_p.parameters(), lr=learning_rate_p)
loss_p = MSELoss()

In [13]:
# Convert to torch.tensor
inputs_p = torch.from_numpy(X_train_p).float()
labels_p = torch.from_numpy(Y_train_p).float()

if __name__ == "__main__":
    for i in range(epochs_p):
        
        # removes gradients from previous iteration
        model_p.zero_grad()
        # Feed Forward
        pred_p = model_p(inputs_p)
        # calculate cost
        errors_p = loss(pred_p, labels_p)
        print(f"loss of iteration {i+1}: {errors_p}")
        # Backpropagation
        errors_p.backward()
        # Update parameters
        optimizer_p.step()
    

loss of iteration 1: 42921452.0
loss of iteration 2: 42920088.0
loss of iteration 3: 42918720.0
loss of iteration 4: 42917356.0
loss of iteration 5: 42915992.0
loss of iteration 6: 42914612.0
loss of iteration 7: 42913244.0
loss of iteration 8: 42911848.0
loss of iteration 9: 42910472.0
loss of iteration 10: 42909076.0
loss of iteration 11: 42907676.0
loss of iteration 12: 42906268.0
loss of iteration 13: 42904848.0
loss of iteration 14: 42903424.0
loss of iteration 15: 42902000.0
loss of iteration 16: 42900552.0
loss of iteration 17: 42899100.0
loss of iteration 18: 42897636.0
loss of iteration 19: 42896160.0
loss of iteration 20: 42894672.0
loss of iteration 21: 42893176.0
loss of iteration 22: 42891664.0
loss of iteration 23: 42890136.0
loss of iteration 24: 42888596.0
loss of iteration 25: 42887044.0
loss of iteration 26: 42885468.0
loss of iteration 27: 42883884.0
loss of iteration 28: 42882280.0
loss of iteration 29: 42880652.0
loss of iteration 30: 42879020.0
loss of iteration 3

loss of iteration 298: 31209604.0
loss of iteration 299: 31032126.0
loss of iteration 300: 30853134.0
loss of iteration 301: 30672648.0
loss of iteration 302: 30490700.0
loss of iteration 303: 30307318.0
loss of iteration 304: 30122526.0
loss of iteration 305: 29936370.0
loss of iteration 306: 29748864.0
loss of iteration 307: 29560060.0
loss of iteration 308: 29369976.0
loss of iteration 309: 29178662.0
loss of iteration 310: 28986150.0
loss of iteration 311: 28792484.0
loss of iteration 312: 28597700.0
loss of iteration 313: 28401838.0
loss of iteration 314: 28204948.0
loss of iteration 315: 28007068.0
loss of iteration 316: 27808252.0
loss of iteration 317: 27608538.0
loss of iteration 318: 27407980.0
loss of iteration 319: 27206628.0
loss of iteration 320: 27004530.0
loss of iteration 321: 26801732.0
loss of iteration 322: 26598294.0
loss of iteration 323: 26394268.0
loss of iteration 324: 26189716.0
loss of iteration 325: 25984678.0
loss of iteration 326: 25779226.0
loss of iterat

loss of iteration 639: 8412075.0
loss of iteration 640: 8406990.0
loss of iteration 641: 8401917.0
loss of iteration 642: 8396853.0
loss of iteration 643: 8391801.0
loss of iteration 644: 8386759.5
loss of iteration 645: 8381727.5
loss of iteration 646: 8376706.0
loss of iteration 647: 8371695.5
loss of iteration 648: 8366695.0
loss of iteration 649: 8361705.5
loss of iteration 650: 8356725.0
loss of iteration 651: 8351754.5
loss of iteration 652: 8346794.5
loss of iteration 653: 8341845.5
loss of iteration 654: 8336905.0
loss of iteration 655: 8331973.5
loss of iteration 656: 8327054.5
loss of iteration 657: 8322145.5
loss of iteration 658: 8317245.5
loss of iteration 659: 8312355.0
loss of iteration 660: 8307474.0
loss of iteration 661: 8302603.5
loss of iteration 662: 8297743.0
loss of iteration 663: 8292891.0
loss of iteration 664: 8288050.0
loss of iteration 665: 8283217.0
loss of iteration 666: 8278396.5
loss of iteration 667: 8273582.0
loss of iteration 668: 8268779.0
loss of it

loss of iteration 1035: 7011701.5
loss of iteration 1036: 7009345.5
loss of iteration 1037: 7006990.5
loss of iteration 1038: 7004643.0
loss of iteration 1039: 7002297.0
loss of iteration 1040: 6999956.5
loss of iteration 1041: 6997618.5
loss of iteration 1042: 6995286.0
loss of iteration 1043: 6992956.5
loss of iteration 1044: 6990632.5
loss of iteration 1045: 6988310.5
loss of iteration 1046: 6985993.0
loss of iteration 1047: 6983680.0
loss of iteration 1048: 6981371.0
loss of iteration 1049: 6979064.5
loss of iteration 1050: 6976764.5
loss of iteration 1051: 6974467.0
loss of iteration 1052: 6972172.5
loss of iteration 1053: 6969883.0
loss of iteration 1054: 6967596.0
loss of iteration 1055: 6965314.5
loss of iteration 1056: 6963035.0
loss of iteration 1057: 6960760.5
loss of iteration 1058: 6958490.0
loss of iteration 1059: 6956222.0
loss of iteration 1060: 6953960.0
loss of iteration 1061: 6951700.0
loss of iteration 1062: 6949443.5
loss of iteration 1063: 6947191.0
loss of iterat

loss of iteration 1437: 6256215.5
loss of iteration 1438: 6254533.5
loss of iteration 1439: 6252851.0
loss of iteration 1440: 6251168.5
loss of iteration 1441: 6249485.0
loss of iteration 1442: 6247801.5
loss of iteration 1443: 6246117.5
loss of iteration 1444: 6244434.5
loss of iteration 1445: 6242751.5
loss of iteration 1446: 6241067.5
loss of iteration 1447: 6239383.0
loss of iteration 1448: 6237700.0
loss of iteration 1449: 6236014.0
loss of iteration 1450: 6234330.0
loss of iteration 1451: 6232645.5
loss of iteration 1452: 6230962.0
loss of iteration 1453: 6229276.5
loss of iteration 1454: 6227589.5
loss of iteration 1455: 6225904.5
loss of iteration 1456: 6224219.0
loss of iteration 1457: 6222533.5
loss of iteration 1458: 6220847.5
loss of iteration 1459: 6219160.0
loss of iteration 1460: 6217473.0
loss of iteration 1461: 6215787.5
loss of iteration 1462: 6214100.5
loss of iteration 1463: 6212412.5
loss of iteration 1464: 6210725.0
loss of iteration 1465: 6209036.5
loss of iterat

...

loss of iteration 48608: 2118940.75
loss of iteration 48609: 2118930.25
loss of iteration 48610: 2118919.75
loss of iteration 48611: 2118909.5
loss of iteration 48612: 2118898.5
loss of iteration 48613: 2118888.5
loss of iteration 48614: 2118878.0
loss of iteration 48615: 2118867.25
loss of iteration 48616: 2118856.75
loss of iteration 48617: 2118846.75
loss of iteration 48618: 2118836.25
loss of iteration 48619: 2118825.75
loss of iteration 48620: 2118815.25
loss of iteration 48621: 2118804.75
loss of iteration 48622: 2118794.25
loss of iteration 48623: 2118784.25
loss of iteration 48624: 2118773.75
loss of iteration 48625: 2118763.5
loss of iteration 48626: 2118752.75
loss of iteration 48627: 2118742.25
loss of iteration 48628: 2118731.75
loss of iteration 48629: 2118721.5
loss of iteration 48630: 2118710.5
loss of iteration 48631: 2118701.0
loss of iteration 48632: 2118689.75
loss of iteration 48633: 2118679.5
loss of iteration 48634: 2118669.25
loss of iteration 48635: 2118658.75
l

loss of iteration 48954: 2115335.25
loss of iteration 48955: 2115325.25
loss of iteration 48956: 2115315.0
loss of iteration 48957: 2115304.75
loss of iteration 48958: 2115294.0
loss of iteration 48959: 2115283.75
loss of iteration 48960: 2115273.5
loss of iteration 48961: 2115263.25
loss of iteration 48962: 2115252.5
loss of iteration 48963: 2115242.5
loss of iteration 48964: 2115232.0
loss of iteration 48965: 2115221.25
loss of iteration 48966: 2115211.0
loss of iteration 48967: 2115200.5
loss of iteration 48968: 2115189.75
loss of iteration 48969: 2115180.0
loss of iteration 48970: 2115169.0
loss of iteration 48971: 2115158.75
loss of iteration 48972: 2115148.0
loss of iteration 48973: 2115138.0
loss of iteration 48974: 2115127.75
loss of iteration 48975: 2115118.0
loss of iteration 48976: 2115107.25
loss of iteration 48977: 2115096.75
loss of iteration 48978: 2115086.5
loss of iteration 48979: 2115076.5
loss of iteration 48980: 2115065.75
loss of iteration 48981: 2115055.0
loss of 

loss of iteration 49267: 2112090.75
loss of iteration 49268: 2112080.25
loss of iteration 49269: 2112070.25
loss of iteration 49270: 2112059.5
loss of iteration 49271: 2112048.75
loss of iteration 49272: 2112038.75
loss of iteration 49273: 2112028.25
loss of iteration 49274: 2112018.25
loss of iteration 49275: 2112008.0
loss of iteration 49276: 2111997.75
loss of iteration 49277: 2111987.0
loss of iteration 49278: 2111977.25
loss of iteration 49279: 2111966.5
loss of iteration 49280: 2111956.0
loss of iteration 49281: 2111946.0
loss of iteration 49282: 2111936.25
loss of iteration 49283: 2111925.75
loss of iteration 49284: 2111915.0
loss of iteration 49285: 2111904.75
loss of iteration 49286: 2111894.25
loss of iteration 49287: 2111883.5
loss of iteration 49288: 2111873.75
loss of iteration 49289: 2111863.5
loss of iteration 49290: 2111853.0
loss of iteration 49291: 2111842.25
loss of iteration 49292: 2111832.25
loss of iteration 49293: 2111822.25
loss of iteration 49294: 2111811.25
lo

loss of iteration 49600: 2108657.0
loss of iteration 49601: 2108646.75
loss of iteration 49602: 2108637.0
loss of iteration 49603: 2108626.0
loss of iteration 49604: 2108615.75
loss of iteration 49605: 2108605.25
loss of iteration 49606: 2108595.0
loss of iteration 49607: 2108585.0
loss of iteration 49608: 2108574.5
loss of iteration 49609: 2108564.25
loss of iteration 49610: 2108555.25
loss of iteration 49611: 2108544.0
loss of iteration 49612: 2108534.0
loss of iteration 49613: 2108523.5
loss of iteration 49614: 2108513.25
loss of iteration 49615: 2108503.0
loss of iteration 49616: 2108492.75
loss of iteration 49617: 2108482.5
loss of iteration 49618: 2108472.5
loss of iteration 49619: 2108461.75
loss of iteration 49620: 2108451.5
loss of iteration 49621: 2108441.0
loss of iteration 49622: 2108430.75
loss of iteration 49623: 2108420.5
loss of iteration 49624: 2108410.25
loss of iteration 49625: 2108399.75
loss of iteration 49626: 2108390.0
loss of iteration 49627: 2108379.75
loss of 

loss of iteration 49938: 2105192.75
loss of iteration 49939: 2105182.25
loss of iteration 49940: 2105172.0
loss of iteration 49941: 2105162.0
loss of iteration 49942: 2105151.75
loss of iteration 49943: 2105141.75
loss of iteration 49944: 2105131.5
loss of iteration 49945: 2105120.75
loss of iteration 49946: 2105111.0
loss of iteration 49947: 2105100.5
loss of iteration 49948: 2105090.75
loss of iteration 49949: 2105080.5
loss of iteration 49950: 2105070.5
loss of iteration 49951: 2105060.0
loss of iteration 49952: 2105050.0
loss of iteration 49953: 2105039.5
loss of iteration 49954: 2105029.25
loss of iteration 49955: 2105019.0
loss of iteration 49956: 2105009.0
loss of iteration 49957: 2104998.75
loss of iteration 49958: 2104988.25
loss of iteration 49959: 2104977.75
loss of iteration 49960: 2104968.0
loss of iteration 49961: 2104958.0
loss of iteration 49962: 2104947.25
loss of iteration 49963: 2104937.25
loss of iteration 49964: 2104927.0
loss of iteration 49965: 2104916.5
loss of 

In [14]:
# Convert to torch.tensor
test_inputs_p = torch.from_numpy(X_test_p).float()
test_labels_p = torch.from_numpy(Y_test_p).float()

# Eval mode
model_p.eval()

#predict and print r2
with torch.no_grad():
    test_pred_p = model_p(test_inputs_p)
    r2_p = r2score(test_pred_p, test_labels_p)
    print(r2_p.item())

0.9352728724479675


This looks even better! I think this model is ready for use. Before we save the model, lets record the observations in the table below:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |
| Polynomial Regression | Cost is smaller but still large. This is no issue | 93% |

In [15]:
if __name__ == "__main__":
    torch.save(model_p.state_dict(), "gpu-predictor.pt")

## References

1. https://www.alliedmarketresearch.com/graphic-processing-unit-market
2. https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module